In [1]:
import warnings
import os

from sympy import Symbol
from numpy.testing import assert_allclose
import numpy as np
from pycalphad import Database, Model, calculate, equilibrium, EquilibriumError, ConditionError
from pycalphad.codegen.callables import build_callables
from pycalphad.core.solver import SolverBase, Solver
from pycalphad.core.utils import get_state_variables
import pycalphad.variables as v
from pycalphad.tests.datasets import *

warnings.simplefilter("always", UserWarning) # so we can test warnings


In [2]:
import pycalphad
pycalphad

<module 'pycalphad' from '/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/__init__.py'>

In [3]:
AL2O3_ND2O3_ZRO2_DBF = Database(AL2O3_ND2O3_ZRO2_TDB)
alfeo=Database("Al-Fe-O_Lindwall_etal.TDB")

/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/io/tdb.py:974: UserWarning: The type definition character `W` was defined in the following phases: ['BCC_B2'], but no corresponding TYPE_DEFINITION line was found in the TDB.
  warnings.warn(f"The type definition character `{typechar}` was defined in the following phases: "


In [4]:
def test_charge_balance_constraint():
    """Phases with charged species are correctly calculated and charged balanced in equilibrium"""
    comps = ['FE', 'AL', 'O', 'VA']
    #phases = list(AL2O3_ND2O3_ZRO2_DBF.phases.keys())
    phases = ['HALITE']
    conds = {v.P: 101325, v.N: 1, v.T: 500, v.X('FE'): 0.2, v.X('O'): 0.6}
    # Higher point density is required for convergence. Lower point densities
    # Can result in either no phases, or only FLUO phase (incorrect)
    res = equilibrium(alfeo, comps, phases, conds, calc_opts={'pdens':2000}, verbose=True)
    #result = calculate(alfeo, comps, phases, P=101325, T=500, output='GM')
    # Values below checked with Thermo-Calc
    #print('result',result)
    print('a=',res.GM.values)
    print(res.Y.values.squeeze())
    #assert np.allclose(res.NP.values.squeeze()[:2], [0.30164254, 0.69835646])
    # site fractions of ND2O3_A
    Y_ND2O3_A = res.Y.values.squeeze()[0, :5]
    Y_PYRO = res.Y.values.squeeze()[1, :]
    SPEC_CHG_ND2O3_A = np.array([3, 4, -2, -2, 0])  # (ND+3,ZR+4):(O-2):(O-2,VA)
    SITE_RATIO_ND2O3_A = np.array([2, 2, 3, 1, 1])  # 2:3:1
    SPEC_CHG_PYRO = np.array([3, 4, 3, 4, -2, 0, -2, -2, 0])  # (ND+3,ZR+4):(ND+3,ZR+4):(O-2,VA):(O-2):(O-2,VA)
    SITE_RATIO_PYRO = np.array([2, 2, 2, 2, 6, 6, 1, 1, 1])  # 2:2:6:1:1
    CHG_ND2O3_A = np.dot(Y_ND2O3_A*SPEC_CHG_ND2O3_A, SITE_RATIO_ND2O3_A)
    CHG_PYRO = np.dot(Y_PYRO*SPEC_CHG_PYRO, SITE_RATIO_PYRO)
    print('CHARGE ND2O3_A', CHG_ND2O3_A)
    print('CHARGE PYRO', CHG_PYRO)
    #assert np.isclose(CHG_ND2O3_A, 0)
    #assert np.isclose(CHG_PYRO, 0)
    print(Y_ND2O3_A)
    assert np.allclose(Y_ND2O3_A, [9.79497936e-01, 2.05020639e-02, 1.00000000e+00, 2.05020639e-02, 9.79497936e-01], rtol=5e-4)
    assert np.allclose(Y_PYRO, [9.99970071e-01, 2.99288042e-05, 3.83395063e-02, 9.61660494e-01, 9.93381787e-01, 6.61821340e-03, 1.00000000e+00, 1.39970285e-03, 9.98600297e-01], rtol=5e-4)


In [5]:
a=test_charge_balance_constraint()

Components: AL AL+3 AL1O1 AL1O2 AL2 AL2FE1O4 AL2O AL2O1 AL2O2 AL2O3 ALO ALO2 ALO3/2 FE FE+2 FE+3 FE+4 FE1O1 FE1O2 FE2 FE2O3 FEO FEO3/2 O O-2 O2 O3 VA
Phases: [HALITE0AL_POS3 + HALITE0FE_POS2 + HALITE0FE_POS3 + HALITE0VA - 1, HALITE1O_NEG2 - 1, 3.0*HALITE0AL_POS3 + 2.0*HALITE0FE_POS2 + 3.0*HALITE0FE_POS3 - 2.0*HALITE1O_NEG2]
HALITE 
[done]
grid [[[[[1.         0.         0.        ]
    [0.         1.         0.        ]
    [0.         0.         1.        ]
    ...
    [0.15655122 0.23641884 0.60702995]
    [0.00653399 0.15626814 0.83719787]
    [0.1284315  0.36471342 0.50685508]]]]] [[[[ 1.00000000e+10  1.00000000e+10  1.00000000e+10 ... -2.26243965e+05
    -6.05891840e+04 -2.48747469e+05]]]]
compset_phases ['N', 'P', 'T', 'X_FE', 'X_O', 'vertex'] [[[[[['' '' '' '']]]]]]
result.intial [[[[[['' '' '' '']]]]]]
num_comps 3
properties.phases [[[[[['HALITE' 'HALITE' 'HALITE' '']]]]]]
prop_Phase_values ['HALITE' 'HALITE' 'HALITE' '']
bulid compset 0 HALITE
bulid compset 1 HALITE
bulid comp

compset 2 0.0 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946) [1.0, 101325.0, 500.0, 0.2939205741474952, 0.028947665097298805, 0.35344764912097326, 0.3236841116393234, 1.0]
idx 2 [0]
compset 0 0.6000000000067784 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439) [1.0, 101325.0, 500.0, 0.3333333333333504, 1.3394387331318481e-14, 0.33333333333331217, 0.33333333334645043, 0.9999999999999997]
idx 0 [0]
compset 1 0.0 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857) [1.0, 101325.0, 500.0, 0.33328937304604384, 3.094774070637246e-05, 0.3333566617934841, 0.33332301741975534, 0.9999999999999999]
idx 1 [0]
compset 2 0.0 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946) [1.0, 101325.0, 500.0, 0.3146483119993434, 0.01314126694807696, 0.3432575100352728, 0.32895291102239743, 

compset 1 0.0 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857) [1.0, 101325.0, 500.0, 0.002489197311311241, 0.9698234789695702, 0.017628483375642656, 0.010058840343470668, 0.9999999999999992]
idx 1 [0]
compset 2 0.0 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946) [1.0, 101325.0, 500.0, 0.0018665340923834943, 0.9971361850373671, 4.267588270500693e-05, 0.0009546049926320481, 1.0]
idx 2 [0]
compset 0 0.599999999959404 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439) [1.0, 101325.0, 500.0, 0.3333333333333339, 8.744329728557674e-12, 0.33333333333333687, 0.33333333336112214, 0.9999999999999999]
idx 0 [0]
compset 1 0.0 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857) [1.0, 101325.0, 500.0, 0.03721990104185237, 0.4226500504638574, 0.34768006531557627, 0.1924499831787

compset 0 0.6000000008104617 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439) [1.0, 101325.0, 500.0, 0.33333333342684257, 3.436287445523863e-10, 0.3333333330107419, 0.33333333327840226, 0.9999999999999998]
idx 0 [0]
compset 1 0.0 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857) [1.0, 101325.0, 500.0, 0.03366108553869493, 0.6837055507387166, 0.1772018806354898, 0.1054314830870884, 0.9999999999999988]
idx 1 [0]
compset 2 0.0 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946) [1.0, 101325.0, 500.0, 0.019220376271312387, 0.9657722259728356, 0.00359813974679727, 0.011409258014139915, 1.0]
idx 2 [0]
compset 0 0.5999999999836456 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439) [1.0, 101325.0, 500.0, 0.333333333333344, 3.436287445523863e-12, 0.33333333333340287, 0.3333333

idx 1 [0]
compset 2 0.0 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946) [1.0, 101325.0, 500.0, 0.11823702947073528, 0.4095231252701671, 0.2754142203491508, 0.19682562491502376, 0.9999999999999998]
idx 2 [0]
compset 0 0.5999999999578669 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439) [1.0, 101325.0, 500.0, 0.3333333333332498, 9.07882330475594e-12, 0.3333333333335689, 0.33333333342421356, 0.9999999999999994]
idx 0 [0]
compset 1 0.0 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857) [1.0, 101325.0, 500.0, 0.20370669918499637, 0.6794036466211342, 0.010024203067580076, 0.1068654511262788, 0.999999999999999]
idx 1 [0]
compset 2 0.0 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946) [1.0, 101325.0, 500.0, 0.17853309842495063, 0.01655673870819674, 0.47709574243624875, 0

...

largest_df1 82331.18247976276
largest_df1 82332.3366769001
largest_df1 82333.4880857617
largest_df1 82334.63671010517
largest_df1 82335.78255367046
largest_df1 82336.92562018032
largest_df1 82338.06591333976
largest_df1 82339.20343683686
largest_df1 82340.33819434233
largest_df1 82341.47018951
largest_df1 82342.5994259766
largest_df1 82343.72590736212
largest_df1 82344.84963726965
largest_df1 82345.97061928565
largest_df1 82347.08885698006
largest_df1 82348.20435390621
largest_df1 82349.31711360111
largest_df1 82350.42713958552
largest_df1 82351.53443536378
largest_df1 82352.63900442427
largest_df1 82353.74085023941
largest_df1 82354.83997626539
largest_df1 82355.9363859428
largest_df1 82357.03008269635
largest_df1 82358.121069935
largest_df1 82359.20935105221
largest_df1 82360.29492942587
largest_df1 82361.37780841865
largest_df1 82362.45799137733
largest_df1 82363.53548163406
largest_df1 82364.61028250528
largest_df1 82365.68239729272
largest_df1 82366.75182928285
largest_df1 82367.8

largest_df1 9514.001680320769
largest_df1 9515.704208788957
largest_df1 9517.402926044539
largest_df1 9519.097841470124
largest_df1 9520.788964388368
largest_df1 9522.476304062904
largest_df1 9524.159869697905
largest_df1 9525.839670439746
largest_df1 9527.515715376765
largest_df1 9529.188013540086
largest_df1 9530.856573903991
largest_df1 9532.521405386738
largest_df1 9534.182516850356
largest_df1 9535.839917101985
largest_df1 9537.493614893872
largest_df1 9539.143618924078
largest_df1 9540.789937836467
largest_df1 9542.432580221794
largest_df1 9544.071554617985
largest_df1 9545.706869510293
largest_df1 9547.338533332106
largest_df1 9548.966554465354
largest_df1 9550.590941240604
largest_df1 9552.211701937806
largest_df1 9553.828844787116
largest_df1 9555.442377968255
largest_df1 9557.0523096119
largest_df1 9558.658647799864
largest_df1 9560.261400564865
largest_df1 9561.86057589209
largest_df1 9563.456181718706
largest_df1 9565.048225934646
largest_df1 9566.636716382578
largest_df1 9

largest_df1 81204.09687274045
largest_df1 81210.2259360548
largest_df1 81216.18036083438
largest_df1 81221.9852066878
largest_df1 81227.65921060223
largest_df1 81233.21691614052
largest_df1 81238.66994164325
largest_df1 81244.02778323257
largest_df1 81249.29834823057
largest_df1 81254.48832346834
largest_df1 81259.60343782973
largest_df1 81264.64865447971
largest_df1 81269.62831485321
largest_df1 81274.54624865213
largest_df1 81279.40585932776
largest_df1 81284.21019151868
largest_df1 81288.96198497052
largest_df1 81293.6637181637
largest_df1 81298.3176439929
largest_df1 81302.92581923131
largest_df1 81307.49012907638
largest_df1 81312.01230776205
largest_df1 81316.49395599586
largest_df1 81320.9365558099
largest_df1 81325.3414832872
largest_df1 81329.71001953128
largest_df1 81334.04336017146
largest_df1 81338.34262364052
largest_df1 81342.60885841685
largest_df1 81346.84304938809
largest_df1 81351.04612346523
largest_df1 81355.21895455508
largest_df1 81359.36236797948
largest_df1 8136

largest_df1 82545.72113511033
largest_df1 82546.23928935191
largest_df1 82546.7552316027
largest_df1 82547.26896300595
largest_df1 82547.78048469947
largest_df1 82548.28979781482
largest_df1 82548.79690347769
largest_df1 82549.30180280824
largest_df1 82549.80449692052
largest_df1 82550.304986923
largest_df1 82550.80327391822
largest_df1 82551.29935900308
largest_df1 82551.79324326856
largest_df1 82552.28492780004
largest_df1 82552.7744136771
largest_df1 82553.26170197368
largest_df1 82553.74679375804
largest_df1 82554.22969009267
largest_df1 82554.71039203438
largest_df1 82555.18890063462
largest_df1 82555.66521693883
largest_df1 82556.13934198697
largest_df1 82556.61127681355
largest_df1 82557.08102244732
largest_df1 82557.54857991153
largest_df1 82558.0139502238
largest_df1 82558.4771343962
largest_df1 82558.93813343553
largest_df1 82559.39694834268
largest_df1 82559.8535801133
largest_df1 82560.30802973738
largest_df1 82560.76029819966
largest_df1 82561.21038647924
largest_df1 82561

ValueError: operands could not be broadcast together with shapes (5,) (9,) 

In [ ]:
a=test_charge_balance_constraint()

In [ ]:
model=Model(AL2O3_ND2O3_ZRO2_DBF,comps = ['ND', 'ZR', 'O', 'VA'],phase_name = 'ND2O3_A')

In [2]:
          ys=ys-chargefact*phr(jj)%invmat(nj,phr(jj)%idim)*&
               phr(jj)%curd%netcharge

SyntaxError: invalid syntax (2914376038.py, line 1)

In [6]:
import warnings
import os
import pytest
from sympy import Symbol
from numpy.testing import assert_allclose
import numpy as np
from pycalphad import Database, Model, calculate, equilibrium, EquilibriumError, ConditionError
from pycalphad.codegen.callables import build_callables, build_phase_records
from pycalphad.core.solver import SolverBase, Solver
from pycalphad.core.utils import get_state_variables, instantiate_models
import pycalphad.variables as v
from pycalphad.tests.datasets import *
ROSE_DBF = Database(ROSE_TDB)
ALFE_DBF = Database(ALFE_TDB)
ALNIFCC4SL_DBF = Database(ALNIFCC4SL_TDB)
ALCOCRNI_DBF = Database(ALCOCRNI_TDB)
ISSUE43_DBF = Database(ISSUE43_TDB)
TOUGH_CHEMPOT_DBF = Database(ALNI_TOUGH_CHEMPOT_TDB)
NI_AL_DUPIN_2001_DBF = Database(NI_AL_DUPIN_2001_TDB)
CUO_DBF = Database(CUO_TDB)
PBSN_DBF = Database(PBSN_TDB)
AL_PARAMETER_DBF = Database(AL_PARAMETER_TDB)
CUMG_PARAMETERS_DBF = Database(CUMG_PARAMETERS_TDB)


@pytest.mark.solver
def test_rose_nine():
    "Nine-component rose diagram point equilibrium calculation."
    my_phases_rose = ['TEST']
    comps = ['H', 'HE', 'LI', 'BE', 'B', 'C', 'N', 'O', 'F']
    conds = dict({v.T: 1000, v.P: 101325})
    for comp in comps[:-1]:
        conds[v.X(comp)] = 1.0/float(len(comps))
    eqx = equilibrium(ROSE_DBF, comps, my_phases_rose, conds, verbose=True)
    assert_allclose(eqx.GM.values.flat[0], -5.8351e3, atol=0.1)


@pytest.mark.solver
def test_eq_binary():
    "Binary phase diagram point equilibrium calculation with magnetism."
    my_phases = ['AL13FE4']
    comps = ['AL', 'FE', 'VA']
    conds = {v.T: 1400, v.P: 101325, v.X('AL'): 0.55}
    eqx = equilibrium(ALFE_DBF, comps, my_phases, conds, verbose=True)
    assert_allclose(eqx.GM.values.flat[0], -9.608807e4)
def test_eq_single_phase():
    "Equilibrium energy should be the same as for a single phase with no miscibility gaps."
    res = calculate(ALFE_DBF, ['AL', 'FE'], 'LIQUID', T=[1400, 2500], P=101325,
                    points={'LIQUID': [[0.1, 0.9], [0.2, 0.8], [0.3, 0.7],
                                       [0.7, 0.3], [0.8, 0.2]]})
    eq = equilibrium(ALFE_DBF, ['AL', 'FE'], 'LIQUID',
                     {v.T: [1400, 2500], v.P: 101325,
                      v.X('AL'): [0.1, 0.2, 0.3, 0.7, 0.8]}, verbose=True)
    assert_allclose(np.squeeze(eq.GM), np.squeeze(res.GM), atol=0.1)


/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/io/tdb.py:974: UserWarning: The type definition character `'` was defined in the following phases: ['FCC_A1'], but no corresponding TYPE_DEFINITION line was found in the TDB.
  warnings.warn(f"The type definition character `{typechar}` was defined in the following phases: "
/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/io/tdb.py:974: UserWarning: The type definition character `%` was defined in the following phases: ['FCC_A1'], but no corresponding TYPE_DEFINITION line was found in the TDB.
  warnings.warn(f"The type definition character `{typechar}` was defined in the following phases: "


In [7]:
test_eq_binary()

Components: AL FE VA
Phases: AL13FE4 
[done]
compset_phases ['N', 'P', 'T', 'X_AL', 'vertex'] [[[[['' '' '']]]]]
result.intial [[[['_FAKE_' '_FAKE_' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4' 'AL13FE4'
    'AL13FE4' 'AL13FE4' 'AL13FE4'

ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [6]:
a=np.array([-1,2,-2,3])

In [1]:
! pytest test_equilibrium.py

============================= test session starts ==============================
platform darwin -- Python 3.9.7, pytest-6.2.5, py-1.10.0, pluggy-1.0.0
rootdir: /Users/sunhui/Desktop/new-charge/pycalphad, configfile: pyproject.toml
plugins: cov-2.12.1
collected 50 items                                                             

test_equilibrium.py ...........F......FF..F...............s....F.FFFF.   [100%]

=================================== FAILURES ===================================
_______________________ test_eq_illcond_magnetic_hessian _______________________

    @pytest.mark.solver
    def test_eq_illcond_magnetic_hessian():
        """
        Check equilibrium of a system with an ill-conditioned Hessian due to magnetism (Tc->0).
        This is difficult to reproduce so we only include some known examples here.
        """
        # This set of conditions is known to trigger the issue
        eq = equilibrium(ALFE_DBF, ['AL', 'FE', 'VA'], ['FCC_A1', 'AL13FE4'],
          

 CompositionSet(AL13FE4, [0.75751514 0.24248486], NP=1e-06, GM=-35805.854396523304)]
site [1.00000000e+00 1.00000000e+05 3.00000000e+02 9.99999961e-01
 3.93890037e-08 1.00000000e+00]
len 6 4
compset [CompositionSet(FCC_A1, [0.8 0.2], NP=1.0, GM=-17803.320902447096)
 CompositionSet(AL13FE4, [0.75751514 0.24248486], NP=1e-06, GM=-35805.854396523304)]
site [1.00000000e+00 1.00000000e+05 3.00000000e+02 1.00000000e+00
 1.00000000e+00 5.98012292e-10 1.32327322e-13]
len 7 6
charge_factor
Yes2 5.975652276464285e-10
Yes3
ori_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 9.99998607e-01
 1.39317189e-06 1.00000000e+00]
change_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 9.99998607e-01
 1.39317189e-06 1.00000000e+00]
ori_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 1.00000000e+00
 1.00000000e+00 4.47064623e-13 1.00000000e-14]
change_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 1.00000000e+00
 1.00000000e+00 4.47064623e-13 1.00000000e-14]
compset [CompositionSet(FCC_A1, [0.8 0.2], NP=1.0,

site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.67553772e-10
 1.34077809e-10 2.00213945e-10 9.99999999e-01 2.67553772e-10
 1.34077982e-10 2.00214110e-10 9.99999999e-01 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.67553772e-10
 1.34077809e-10 2.00213945e-10 9.99999999e-01 2.67553772e-10
 1.34077963e-10 2.00214107e-10 9.99999999e-01 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5

 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.3775

ori_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
change_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
ori_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
change_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
ori_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 5.67247455e-01
 4.22023438e-01 1.07291064e-02]
change_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 5.67247455e-01
 4.22023438e-01 1.07291064e-02]
compset [CompositionSet(BCC_B2, [

compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 9.55844186e-11
 4.78997149e-11 7.15270555e-11 1.00000000e+00 9.55844186e-11
 4.78997149e-11 7.15270555e-11 1.00000000e+00 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LI

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [9]:
x=a[2:]/2

In [18]:
a[1:].*a[1:]

SyntaxError: invalid syntax (3380728885.py, line 1)